In [14]:
import os
import json
import pickle
import pydot
import copy
import networkx as nx
from networkx.drawing.nx_pydot import graphviz_layout
import matplotlib.pyplot as plt


In [15]:
def make_hierarchical_tree_of_brain_regions(path_to_ontology_json):
    '''
    Explore the hierarchical structure of brain regions by making
    walks across the branches of the tree.
    
    At each walk we start at the root, and stop when
    (1) either there are no more children
    (2) or we ended up at an edge that we already incorporated.
    
    When we stop, we append the last walked edge into the edges dictionary.
    
    We stop starting the walks if we are at the root, and have nowhere to go
    (because we already walked on all departing edges).
    
    Input
    -----
    path_to_ontology_json (string)
    Path to AllenMouseBrainOntology.json file.
    
    Outputs
    -------
    edges (dict)
    Dictionary with all child regions as keys, and the parent it is connected to as values.
    Since the hierarchy is a tree, every child is connected to one parent only.
    
    brain_region_dict(dict)
    Dictionary with the region acronyms (abbreviations) as keys, and the corresponding full region name
    as value.
    '''


    # open the JSON file 
    allen_data = open(path_to_ontology_json,) 

    # deserailize the data
    allen_data = json.load(allen_data)
    brain_atlas = allen_data['msg'][0]

    edges = {}
    brain_region_dict = {'root': 'root'}
    make_another_walk = True

    while make_another_walk:

        # we start at the root
        curr_region = copy.deepcopy(brain_atlas) 
        walking = True

        while walking:

            children = curr_region['children']  # list of children dictionaries
            new_node = curr_region['acronym']   # acronym of brain region, e.g. 'AVA'
            made_step = False

            # Loop over edges starting from the current node
            for child_region in children:
                child_name = child_region['acronym']

                # Put child name in region_dict
                if child_name not in list(brain_region_dict.keys()):
                    brain_region_dict[child_name] = child_region['name']

                # Check whether we already walked on this edge.
                # If we didn't, move make a step to the child node.
                if not(child_name in list(edges.keys())):
                    curr_region = child_region
                    made_step = True
                    break

            # If we didn't manage to make a step because we already walked on 
            # all edges departing from the current node, add the edge of the new_node to the old node
            if not(made_step):
                child_name = new_node  # the new node is the child
                parent_name = node     # the old node (from the previous loop) is the parent
            # If we did make a step, add the edge of the child region to the new_node
            else:
                parent_name = new_node # the new node is the parent

            walking = (len(children) > 0) and made_step
            node = new_node            # save the name of the old node

            # Stop if you are still at the root and can no longer make a step
            if not(walking) and node=='root':
                make_another_walk = False

        # Append the last edge of the walk
        edges[child_name] = parent_name
        
    return edges,brain_region_dict

#%%
def edges_to_tree(region_edges):
    '''
    Converts a dictionary with edges to a tree dictionary.
    In a tree dictionary, all parent regions are the keys,
    and the subregions that belong to the parent are stored
    in a list as the value corresponding to the key.
    
    Example:
    tree_dict['ACA'] = ['ACAv', 'ACAd'] # (dorsal and ventral part)
    tree_dict['ACAv'] = ['ACAv5', 'ACAv2/3', 'ACAv6a', 'ACAv1', 'ACAv6b'] # all layers in ventral part
    '''

    # Convert the edges into a tree
    tree_dict = {}
    for child, parent in region_edges.items():
        if parent in tree_dict:
            tree_dict[parent].append(child)
        else:
            tree_dict[parent] = [child]
    
    return tree_dict

#%%
def tree_dict_to_graph(tree_dict, region_dict, show_abbreviations=True):
    '''
    Convert tree dictionary into a networkx graph structure 
    for visualization.
    '''
    T = nx.Graph()
    for parent, children_list in tree_dict.items():
        parent_name = region_dict[parent].replace(' ', '\n')
        for child in children_list:
            child_name = region_dict[child].replace(' ', '\n')
            if show_abbreviations:
                T.add_edge(parent, child)
            else:
                T.add_edge(parent_name, child_name)
            
    return T

def plot_tree(T, figsize=(140,50), font_size=12):
    '''
    # Plots a networkx graph (T) as a tree.
    '''
    plt.figure(figsize=figsize)
    pos = graphviz_layout(T, prog="dot")
    nx.draw_networkx_nodes(T, pos)
    nx.draw_networkx_labels(T, pos, font_size=font_size)
    nx.draw_networkx_edges(T, pos)


In [16]:
path_to_ontology_json = '../AllenMouseBrainOntology.json'
output_path = './'
print('Creating tree ...')
edges,brain_region_dict = make_hierarchical_tree_of_brain_regions(path_to_ontology_json)
tree = edges_to_tree(edges)
save_dict = {'BrainOntologyEdges': edges,
             'BrainOntologyTree': tree,
             'BrainOntologyRegions': brain_region_dict}

# save to pickle file
# with open("AllenMouseBrainOntology.pk","wb") as f:
#    pickle.dump(save_dict, f)

# Plot the graph with abbreviations
print('Plotting tree ...')
T = tree_dict_to_graph(tree, brain_region_dict, show_abbreviations=False)
output_file = os.path.join(output_path, 'whole_brain_tree_fullnames.pdf')
plot_tree(T, figsize=(900,170), font_size=5)
# plt.savefig(output_file)

Creating tree ...
Plotting tree ...
